
# 核主成分分析

本示例展示了主成分分析（:class:`~sklearn.decomposition.PCA` ）及其核版本（:class:`~sklearn.decomposition.KernelPCA` ）之间的区别。

一方面，我们展示了 :class:`~sklearn.decomposition.KernelPCA` 能够找到一个线性分离数据的投影，而 :class:`~sklearn.decomposition.PCA` 则不能。

最后，我们展示了使用 :class:`~sklearn.decomposition.KernelPCA` 反转此投影是一个近似值，而使用 :class:`~sklearn.decomposition.PCA` 则是精确的。


In [ ]:
# 作者：scikit-learn 开发者
# SPDX-License-Identifier: BSD-3-Clause

## 投影数据： `PCA` vs. `KernelPCA` 

在本节中，我们展示了在使用主成分分析（PCA）投影数据时使用核的优势。我们创建了一个由两个嵌套圆组成的数据集。



In [ ]:
from sklearn.datasets import make_circles
from sklearn.model_selection import train_test_split

X, y = make_circles(n_samples=1_000, factor=0.3, noise=0.05, random_state=0)
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, random_state=0)

让我们快速浏览一下生成的数据集。



In [ ]:
import matplotlib.pyplot as plt

_, (train_ax, test_ax) = plt.subplots(ncols=2, sharex=True, sharey=True, figsize=(8, 4))

train_ax.scatter(X_train[:, 0], X_train[:, 1], c=y_train)
train_ax.set_ylabel("Feature #1")
train_ax.set_xlabel("Feature #0")
train_ax.set_title("Training data")

test_ax.scatter(X_test[:, 0], X_test[:, 1], c=y_test)
test_ax.set_xlabel("Feature #0")
_ = test_ax.set_title("Testing data")

每个类别的样本不能线性分离：没有一条直线可以将内集合的样本与外集合的样本分开。

现在，我们将使用带核和不带核的PCA来观察使用这种核的效果。这里使用的核是径向基函数（RBF）核。



In [ ]:
from sklearn.decomposition import PCA, KernelPCA

pca = PCA(n_components=2)
kernel_pca = KernelPCA(
    n_components=None, kernel="rbf", gamma=10, fit_inverse_transform=True, alpha=0.1
)

X_test_pca = pca.fit(X_train).transform(X_test)
X_test_kernel_pca = kernel_pca.fit(X_train).transform(X_test)

In [ ]:
fig, (orig_data_ax, pca_proj_ax, kernel_pca_proj_ax) = plt.subplots(
    ncols=3, figsize=(14, 4)
)

orig_data_ax.scatter(X_test[:, 0], X_test[:, 1], c=y_test)
orig_data_ax.set_ylabel("Feature #1")
orig_data_ax.set_xlabel("Feature #0")
orig_data_ax.set_title("Testing data")

pca_proj_ax.scatter(X_test_pca[:, 0], X_test_pca[:, 1], c=y_test)
pca_proj_ax.set_ylabel("Principal component #1")
pca_proj_ax.set_xlabel("Principal component #0")
pca_proj_ax.set_title("Projection of testing data\n using PCA")

kernel_pca_proj_ax.scatter(X_test_kernel_pca[:, 0], X_test_kernel_pca[:, 1], c=y_test)
kernel_pca_proj_ax.set_ylabel("Principal component #1")
kernel_pca_proj_ax.set_xlabel("Principal component #0")
_ = kernel_pca_proj_ax.set_title("Projection of testing data\n using KernelPCA")

我们回顾一下，PCA对数据进行线性变换。直观上，这意味着坐标系将以各分量的方差为基准进行中心化、重新缩放，最后进行旋转。通过这种变换得到的数据是各向同性的，现在可以投影到其*主成分*上。

因此，通过观察使用PCA进行的投影（即中间图），我们看到在缩放方面没有变化；实际上，数据是以零为中心的两个同心圆，原始数据已经是各向同性的。然而，我们可以看到数据已经被旋转。总之，我们看到如果要定义一个线性分类器来区分两个类别的样本，这样的投影不会有帮助。

使用核函数可以进行非线性投影。在这里，通过使用RBF核函数，我们期望投影能够展开数据集，同时大致保持原始空间中彼此接近的数据点对的相对距离。

我们在右图中观察到这种行为：给定类别的样本比来自相反类别的样本更接近彼此，从而解开了两个样本集。现在，我们可以使用线性分类器来区分这两个类别的样本。

## 投影到原始特征空间

在使用 :class:`~sklearn.decomposition.KernelPCA` 时需要注意的一个特点与重构（即在原始特征空间中的反向投影）有关。对于 :class:`~sklearn.decomposition.PCA` ，如果 `n_components` 与原始特征的数量相同，则重构将是精确的。在这个例子中就是这种情况。

我们可以通过使用 :class:`~sklearn.decomposition.KernelPCA` 进行反向投影来调查是否能得到原始数据集。



In [ ]:
X_reconstructed_pca = pca.inverse_transform(pca.transform(X_test))
X_reconstructed_kernel_pca = kernel_pca.inverse_transform(kernel_pca.transform(X_test))

In [ ]:
fig, (orig_data_ax, pca_back_proj_ax, kernel_pca_back_proj_ax) = plt.subplots(
    ncols=3, sharex=True, sharey=True, figsize=(13, 4)
)

orig_data_ax.scatter(X_test[:, 0], X_test[:, 1], c=y_test)
orig_data_ax.set_ylabel("Feature #1")
orig_data_ax.set_xlabel("Feature #0")
orig_data_ax.set_title("Original test data")

pca_back_proj_ax.scatter(X_reconstructed_pca[:, 0], X_reconstructed_pca[:, 1], c=y_test)
pca_back_proj_ax.set_xlabel("Feature #0")
pca_back_proj_ax.set_title("Reconstruction via PCA")

kernel_pca_back_proj_ax.scatter(
    X_reconstructed_kernel_pca[:, 0], X_reconstructed_kernel_pca[:, 1], c=y_test
)
kernel_pca_back_proj_ax.set_xlabel("Feature #0")
_ = kernel_pca_back_proj_ax.set_title("Reconstruction via KernelPCA")

虽然我们看到使用 :class:`~sklearn.decomposition.PCA` 可以完美重建，但对于 :class:`~sklearn.decomposition.KernelPCA` 我们观察到不同的结果。

实际上，:meth:`~sklearn.decomposition.KernelPCA.inverse_transform` 不能依赖于解析的反向投影，因此无法进行精确的重构。相反，内部会训练一个 :class:`~sklearn.kernel_ridge.KernelRidge` 来学习从核PCA基到原始特征空间的映射。因此，这种方法在反向投影到原始特征空间时会引入小的差异，从而带来近似。

为了改进使用 :meth:`~sklearn.decomposition.KernelPCA.inverse_transform` 的重建效果，可以调整 :class:`~sklearn.decomposition.KernelPCA` 中的 `alpha` 参数，该参数是正则化项，用于控制在映射训练过程中对训练数据的依赖程度。

